<a href="https://colab.research.google.com/github/LianaN/SpeechLab/blob/main/bark_demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Install

In [1]:
# install bark (make sure you have torch>=2 for much faster flash-attention)
!pip install git+https://github.com/suno-ai/bark.git

  Cloning https://github.com/suno-ai/bark.git to /tmp/pip-req-build-anhdqfaa
  Running command git clone --filter=blob:none --quiet https://github.com/suno-ai/bark.git /tmp/pip-req-build-anhdqfaa
  Resolved https://github.com/suno-ai/bark.git to commit 56b0ba13f7c281cbffa07ea9abf7b30273a60b6a
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.7/135.7 kB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 21.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 19.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 51.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 39.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.0/11.0 MB 97.1 MB/s eta 0:00:00
     ━━

## Basics

In [2]:
from bark import SAMPLE_RATE, generate_audio, preload_models
from IPython.display import Audio

preload_models()

Downloading: "https://dl.fbaipublicfiles.com/encodec/v0/encodec_24khz-d7cc33bc.th" to /root/.cache/torch/hub/checkpoints/encodec_24khz-d7cc33bc.th
100%|██████████| 88.9M/88.9M [00:00<00:00, 112MB/s]


In [4]:
import numpy as np

In [5]:
speaker_lookup = {"Juan": "v2/es_speaker_5", "Judith": "v2/es_speaker_6"}

# Script generated by chat GPT
script = """
Juan: ¡Hola! ¿Puedo hablar con Judith?
Judith: Sí, soy yo. ¿Quién llama?
Juan: Hola, Judith. [clears throat] Soy Carlos, del restaurante Paput Menorca. Estamos llamando para confirmar su reserva para esta tarde.
Judith: ¿Mi reserva? No tengo ninguna reserva.
Juan: [clears throat] ¿En serio? Tenemos aquí una reserva a su nombre para esta tarde. Estamos preparando una cena especial para usted, con un menú de degustación de 5 platos.
Judith: ¿Qué? No tengo ninguna reserva.
Juan: [clears throat] Bueno, esto es un poco extraño. ¿Podría ser que alguien más haya hecho la reserva en su nombre?
Judith: No lo sé...
Juan: [clears throat] Bueno, entonces, ¿quiere que cancelemos la reserva?
Judith: No, espera... ¿Quién hizo la reserva?
Juan: [clears throat] Bueno, según nuestros registros, la reserva fue hecha por un tal "Sr. Misterioso".
Judith: ¿Sr. Misterioso?
Juan: Sí, eso es lo que dice aquí. [clears throat] Así que, ¿quiere que cancelemos la reserva o quiere que la mantengamos?
"""
script = script.strip().split("\n")
script = [s.strip() for s in script if s]
script

['Juan: ¡Hola! ¿Puedo hablar con Judith?',
 'Judith: Sí, soy yo. ¿Quién llama?',
 'Juan: Hola, Judith. [clears throat] Soy Carlos, del restaurante Paput Menorca. Estamos llamando para confirmar su reserva para esta tarde.',
 'Judith: ¿Mi reserva? No tengo ninguna reserva.',
 'Juan: [clears throat] ¿En serio? Tenemos aquí una reserva a su nombre para esta tarde. Estamos preparando una cena especial para usted, con un menú de degustación de 5 platos.',
 'Judith: ¿Qué? No tengo ninguna reserva.',
 'Juan: [clears throat] Bueno, esto es un poco extraño. ¿Podría ser que alguien más haya hecho la reserva en su nombre?',
 'Judith: No lo sé...',
 'Juan: [clears throat] Bueno, entonces, ¿quiere que cancelemos la reserva?',
 'Judith: No, espera... ¿Quién hizo la reserva?',
 'Juan: [clears throat] Bueno, según nuestros registros, la reserva fue hecha por un tal "Sr. Misterioso".',
 'Judith: ¿Sr. Misterioso?',
 'Juan: Sí, eso es lo que dice aquí. [clears throat] Así que, ¿quiere que cancelemos la r

In [6]:
pieces = []
silence = np.zeros(int(0.5*SAMPLE_RATE))
silence_speaker = np.zeros(int(1.5*SAMPLE_RATE))
silence_speaker_name = "Judith"
for line in script:
    speaker, text = line.split(": ")
    if speaker != silence_speaker_name:
      audio_array = generate_audio(text, history_prompt=speaker_lookup[speaker], )
      pieces += [audio_array, silence.copy()]
    else:
      pieces += [silence_speaker.copy()]

100%|██████████| 32/32 [00:31<00:00,  1.00it/s]


In [7]:
Audio(np.concatenate(pieces), rate=SAMPLE_RATE)

In [8]:
from scipy.io.wavfile import write as write_wav
write_wav("bark_generation.wav", SAMPLE_RATE, np.concatenate(pieces))